#B1
- We use child referencing data model. 
- Reasons
- 1.According to lecture slices, if the number of documents are not very large, we can choose embedding data model and child referencing data model. However, embedding data model is the join result of two collections, it may loss data, for example, if the fire data records information on 2017-9-15, but climate data did not record any data on that day, which will cause fire data loss. The climate file has hundred ducuments and fire file has thousand documents, so it is hard to check whether there exists this phenomenon of lossing data. Therefore we choose child referencing data model.
- 2.For taskB4, most of queries only involve fire data or climate data. Child referencing data model has two collections, we just need to use one collection when the task refers to one file. For embedding data model, if we want to search some document in one file data, we have to operate for whole data because climate and fire data has combined into one collection. Therefore, child referencing data model is a suitable data model to support efficient querying of the two data sets in mongodb.   
- These two files, the fire file has a few thousand documents and the climate file has a few hundred documents, so we use array to keep reference key of the many side (put fire id into climate as the reference key), which is shown below.

In [9]:
# CLIMATE COLLECTION
#      {'Air Temperature(Celcius)': 14,
#       'Date': '2017-04-01',
#       'MAX': '63.9*',
#       'MIN': '50.4',
#       'Max Wind Speed': 15.9,
#       'Precipitation': '0.00I',
#       'Relative Humidity': 45.7,
#       'Station': 948701,
#       'WindSpeed  (knots)': 9.2,
#       '_id': ObjectId('5b024661f5169e0e7d6d706e'),
#       'fire': [{'_id': ObjectId('5b024665f5169e0e7d6d7b34')},
#                {'_id': ObjectId('5b024665f5169e0e7d6d7b35')},
#                {'_id': ObjectId('5b024665f5169e0e7d6d7b36')},
#                {'_id': ObjectId('5b024665f5169e0e7d6d7b37')},
#                {'_id': ObjectId('5b024665f5169e0e7d6d7b38')},
#                {'_id': ObjectId('5b024665f5169e0e7d6d7b39')},
#                {'_id': ObjectId('5b024665f5169e0e7d6d7b3a')}]}

In [10]:
# FIRE COLLECTION
#    {'Confidence': 87,
#     'Date': '2017-03-06',
#     'Datetime': '2017-03-06T05:06:30',
#     'Latitude': -34.3795,
#     'Longitude': 141.6331,
#     'Power': 21.7,
#     'Surface Temperature (Celcius)': 62,
#     'Surface Temperature (kelvin)': 335.4,
#     '_id': ObjectId('5affce7226cc016aa4ad2a6e')}

In [38]:
#B2
import pymongo

In [39]:
from pymongo import MongoClient

In [40]:
client = MongoClient ()

In [13]:
db = client.TaskB_db

In [14]:
myCol1 = db.Climate
myCol2 = db.Fire

In [15]:
#B3
import csv

with open('ClimateData-Part1.csv','r') as csvfile1:
    reader = csv.DictReader(csvfile1)
    for r in reader:
        document = {}
        for k,v in r.items():
            k = k.strip()
            v = v.strip()
            L1 = ["Date","Precipitation",'MAX','MIN']
            L2 = ['Station','Air Temperature(Celcius)']
            if k in L1:
                document[k] = v
            elif k in L2:
                document[k] = int(v)
            else:
                document[k] = float(v)
        document['fire'] = []  
        myCol1.insert_one(document) 
        
with open('FireData-Part1.csv','r') as csvfile2:
    reader = csv.DictReader(csvfile2)
    for r in reader:
        document = {}
        for k,v in r.items():
            k = k.strip()
            v = v.strip()
            L1 = ['Date','Datetime']
            L2 = ['Confidence','Surface Temperature (Celcius)']
            if k in L1:
                document[k] = v
            elif k in L2:
                document[k] = int(v)
            else:
                document[k] = float(v)
        myCol2.insert_one(document)
        myCol1.update_one({"Date":document["Date"]},
                          {"$push":{"fire": {"_id": document["_id"]}}})

In [16]:
from pprint import pprint

results = myCol1.find({})
for document in results: 
    pprint(document)

{'Air Temperature(Celcius)': 19,
 'Date': '2016-12-31',
 'MAX': '72.0*',
 'MIN': '61.9*',
 'Max Wind Speed': 11.1,
 'Precipitation': '0.00I',
 'Relative Humidity': 56.8,
 'Station': 948700,
 'WindSpeed  (knots)': 7.9,
 '_id': ObjectId('5b026118f5169e1072a55bb9'),
 'fire': []}
{'Air Temperature(Celcius)': 15,
 'Date': '2017-01-02',
 'MAX': '72.0*',
 'MIN': '58.3',
 'Max Wind Speed': 13.0,
 'Precipitation': '0.02G',
 'Relative Humidity': 50.7,
 'Station': 948700,
 'WindSpeed  (knots)': 9.2,
 '_id': ObjectId('5b026118f5169e1072a55bba'),
 'fire': []}
{'Air Temperature(Celcius)': 16,
 'Date': '2017-01-03',
 'MAX': '68.4*',
 'MIN': '54.3*',
 'Max Wind Speed': 15.0,
 'Precipitation': '0.00G',
 'Relative Humidity': 53.6,
 'Station': 948700,
 'WindSpeed  (knots)': 8.1,
 '_id': ObjectId('5b026118f5169e1072a55bbb'),
 'fire': []}
{'Air Temperature(Celcius)': 24,
 'Date': '2017-01-04',
 'MAX': '87.3*',
 'MIN': '54',
 'Max Wind Speed': 14.0,
 'Precipitation': '0.00I',
 'Relative Humidity': 61.6,
 'S

 'Precipitation': '0.00I',
 'Relative Humidity': 57.3,
 'Station': 948701,
 'WindSpeed  (knots)': 5.4,
 '_id': ObjectId('5b026118f5169e1072a55bf4'),
 'fire': []}
{'Air Temperature(Celcius)': 20,
 'Date': '2017-03-02',
 'MAX': '75.0*',
 'MIN': '58.1',
 'Max Wind Speed': 15.0,
 'Precipitation': '0.00I',
 'Relative Humidity': 62.6,
 'Station': 948701,
 'WindSpeed  (knots)': 10.1,
 '_id': ObjectId('5b026118f5169e1072a55bf5'),
 'fire': []}
{'Air Temperature(Celcius)': 21,
 'Date': '2017-03-03',
 'MAX': '84.2*',
 'MIN': '60.3*',
 'Max Wind Speed': 21.0,
 'Precipitation': '0.00I',
 'Relative Humidity': 59.5,
 'Station': 948701,
 'WindSpeed  (knots)': 12.4,
 '_id': ObjectId('5b026118f5169e1072a55bf6'),
 'fire': []}
{'Air Temperature(Celcius)': 22,
 'Date': '2017-03-04',
 'MAX': '80.8*',
 'MIN': '59.4',
 'Max Wind Speed': 11.1,
 'Precipitation': '0.00I',
 'Relative Humidity': 62.0,
 'Station': 948701,
 'WindSpeed  (knots)': 7.9,
 '_id': ObjectId('5b026118f5169e1072a55bf7'),
 'fire': []}
{'Air T

          {'_id': ObjectId('5b02611bf5169e1072a566aa')},
          {'_id': ObjectId('5b02611bf5169e1072a566ab')},
          {'_id': ObjectId('5b02611bf5169e1072a566ac')},
          {'_id': ObjectId('5b02611bf5169e1072a566ad')},
          {'_id': ObjectId('5b02611bf5169e1072a566ae')},
          {'_id': ObjectId('5b02611bf5169e1072a566af')},
          {'_id': ObjectId('5b02611bf5169e1072a566b0')},
          {'_id': ObjectId('5b02611bf5169e1072a566b1')},
          {'_id': ObjectId('5b02611bf5169e1072a566b2')},
          {'_id': ObjectId('5b02611bf5169e1072a566b3')},
          {'_id': ObjectId('5b02611bf5169e1072a566b4')},
          {'_id': ObjectId('5b02611bf5169e1072a566b5')},
          {'_id': ObjectId('5b02611bf5169e1072a566b6')},
          {'_id': ObjectId('5b02611bf5169e1072a566b7')},
          {'_id': ObjectId('5b02611bf5169e1072a566b8')},
          {'_id': ObjectId('5b02611bf5169e1072a566b9')},
          {'_id': ObjectId('5b02611bf5169e1072a566ba')},
          {'_id': ObjectId('5b0

{'Air Temperature(Celcius)': 14,
 'Date': '2017-04-10',
 'MAX': '62.4*',
 'MIN': '46.8',
 'Max Wind Speed': 20.0,
 'Precipitation': '0.01G',
 'Relative Humidity': 50.4,
 'Station': 948701,
 'WindSpeed  (knots)': 12.8,
 '_id': ObjectId('5b026118f5169e1072a55c1c'),
 'fire': []}
{'Air Temperature(Celcius)': 14,
 'Date': '2017-04-11',
 'MAX': '65.1*',
 'MIN': '52.2*',
 'Max Wind Speed': 13.0,
 'Precipitation': '0.00G',
 'Relative Humidity': 52.5,
 'Station': 948701,
 'WindSpeed  (knots)': 7.0,
 '_id': ObjectId('5b026118f5169e1072a55c1d'),
 'fire': [{'_id': ObjectId('5b02611af5169e1072a56539')},
          {'_id': ObjectId('5b02611af5169e1072a5653a')},
          {'_id': ObjectId('5b02611af5169e1072a5653b')},
          {'_id': ObjectId('5b02611af5169e1072a5653c')},
          {'_id': ObjectId('5b02611af5169e1072a5653d')},
          {'_id': ObjectId('5b02611af5169e1072a5653e')},
          {'_id': ObjectId('5b02611af5169e1072a5653f')},
          {'_id': ObjectId('5b02611af5169e1072a56540')},
   

          {'_id': ObjectId('5b02611af5169e1072a564ca')},
          {'_id': ObjectId('5b02611af5169e1072a564cb')},
          {'_id': ObjectId('5b02611af5169e1072a564cc')},
          {'_id': ObjectId('5b02611af5169e1072a564cd')},
          {'_id': ObjectId('5b02611af5169e1072a564ce')},
          {'_id': ObjectId('5b02611af5169e1072a564cf')},
          {'_id': ObjectId('5b02611af5169e1072a564d0')},
          {'_id': ObjectId('5b02611af5169e1072a564d1')},
          {'_id': ObjectId('5b02611af5169e1072a564d2')},
          {'_id': ObjectId('5b02611af5169e1072a564d3')},
          {'_id': ObjectId('5b02611af5169e1072a564d4')},
          {'_id': ObjectId('5b02611af5169e1072a564d5')},
          {'_id': ObjectId('5b02611af5169e1072a564d6')},
          {'_id': ObjectId('5b02611af5169e1072a564d7')},
          {'_id': ObjectId('5b02611af5169e1072a564d8')},
          {'_id': ObjectId('5b02611af5169e1072a564d9')},
          {'_id': ObjectId('5b02611af5169e1072a564da')},
          {'_id': ObjectId('5b0

...

 'MAX': '58.1*',
 'MIN': '40.8*',
 'Max Wind Speed': 15.0,
 'Precipitation': '0.00G',
 'Relative Humidity': 40.0,
 'Station': 948701,
 'WindSpeed  (knots)': 8.6,
 '_id': ObjectId('5b026118f5169e1072a55c7b'),
 'fire': [{'_id': ObjectId('5b026118f5169e1072a55e51')},
          {'_id': ObjectId('5b026118f5169e1072a55e52')}]}
{'Air Temperature(Celcius)': 6,
 'Date': '2017-07-15',
 'MAX': '53.4*',
 'MIN': '36.9*',
 'Max Wind Speed': 9.9,
 'Precipitation': '0.00I',
 'Relative Humidity': 37.1,
 'Station': 948701,
 'WindSpeed  (knots)': 5.8,
 '_id': ObjectId('5b026118f5169e1072a55c7c'),
 'fire': []}
{'Air Temperature(Celcius)': 10,
 'Date': '2017-07-16',
 'MAX': '53.4*',
 'MIN': '36.9',
 'Max Wind Speed': 20.0,
 'Precipitation': '0.00I',
 'Relative Humidity': 35.6,
 'Station': 948701,
 'WindSpeed  (knots)': 14.5,
 '_id': ObjectId('5b026118f5169e1072a55c7d'),
 'fire': []}
{'Air Temperature(Celcius)': 12,
 'Date': '2017-07-17',
 'MAX': '59.4*',
 'MIN': '46.6',
 'Max Wind Speed': 21.0,
 'Precipita

 'WindSpeed  (knots)': 6.2,
 '_id': ObjectId('5b026118f5169e1072a55ca7'),
 'fire': []}
{'Air Temperature(Celcius)': 8,
 'Date': '2017-08-28',
 'MAX': '52.7*',
 'MIN': '38.7',
 'Max Wind Speed': 9.9,
 'Precipitation': '0.01G',
 'Relative Humidity': 40.8,
 'Station': 948702,
 'WindSpeed  (knots)': 5.5,
 '_id': ObjectId('5b026118f5169e1072a55ca8'),
 'fire': []}
{'Air Temperature(Celcius)': 10,
 'Date': '2017-08-29',
 'MAX': '55.4*',
 'MIN': '41.2',
 'Max Wind Speed': 8.9,
 'Precipitation': '0.00G',
 'Relative Humidity': 41.4,
 'Station': 948702,
 'WindSpeed  (knots)': 6.9,
 '_id': ObjectId('5b026118f5169e1072a55ca9'),
 'fire': []}
{'Air Temperature(Celcius)': 8,
 'Date': '2017-08-30',
 'MAX': '56.3*',
 'MIN': '36.0*',
 'Max Wind Speed': 13.0,
 'Precipitation': '0.02G',
 'Relative Humidity': 39.3,
 'Station': 948702,
 'WindSpeed  (knots)': 4.7,
 '_id': ObjectId('5b026118f5169e1072a55caa'),
 'fire': []}
{'Air Temperature(Celcius)': 8,
 'Date': '2017-08-31',
 'MAX': '58.5*',
 'MIN': '34.5*',

 'fire': [{'_id': ObjectId('5b026118f5169e1072a55dcf')},
          {'_id': ObjectId('5b026118f5169e1072a55dd0')},
          {'_id': ObjectId('5b026118f5169e1072a55dd1')},
          {'_id': ObjectId('5b026118f5169e1072a55dd2')},
          {'_id': ObjectId('5b026118f5169e1072a55dd3')},
          {'_id': ObjectId('5b026118f5169e1072a55dd4')},
          {'_id': ObjectId('5b026118f5169e1072a55dd5')},
          {'_id': ObjectId('5b026118f5169e1072a55dd6')},
          {'_id': ObjectId('5b026118f5169e1072a55dd7')},
          {'_id': ObjectId('5b026118f5169e1072a55dd8')},
          {'_id': ObjectId('5b026118f5169e1072a55dd9')},
          {'_id': ObjectId('5b026118f5169e1072a55dda')},
          {'_id': ObjectId('5b026118f5169e1072a55ddb')},
          {'_id': ObjectId('5b026118f5169e1072a55ddc')},
          {'_id': ObjectId('5b026118f5169e1072a55ddd')},
          {'_id': ObjectId('5b026118f5169e1072a55dde')},
          {'_id': ObjectId('5b026118f5169e1072a55ddf')},
          {'_id': ObjectId('5b0

 'MAX': '82.6*',
 'MIN': '47.7*',
 'Max Wind Speed': 27.0,
 'Precipitation': '0.24G',
 'Relative Humidity': 44.9,
 'Station': 948702,
 'WindSpeed  (knots)': 16.1,
 '_id': ObjectId('5b026118f5169e1072a55ce6'),
 'fire': []}
{'Air Temperature(Celcius)': 11,
 'Date': '2017-10-30',
 'MAX': '59.2*',
 'MIN': '47.3',
 'Max Wind Speed': 14.0,
 'Precipitation': '0.20G',
 'Relative Humidity': 43.2,
 'Station': 948702,
 'WindSpeed  (knots)': 8.1,
 '_id': ObjectId('5b026118f5169e1072a55ce7'),
 'fire': []}
{'Air Temperature(Celcius)': 13,
 'Date': '2017-10-31',
 'MAX': '60.3*',
 'MIN': '48.9',
 'Max Wind Speed': 12.0,
 'Precipitation': '0.01G',
 'Relative Humidity': 47.1,
 'Station': 948702,
 'WindSpeed  (knots)': 8.1,
 '_id': ObjectId('5b026118f5169e1072a55ce8'),
 'fire': []}
{'Air Temperature(Celcius)': 13,
 'Date': '2017-11-01',
 'MAX': '60.8*',
 'MIN': '52.2*',
 'Max Wind Speed': 12.0,
 'Precipitation': '0.08G',
 'Relative Humidity': 50.1,
 'Station': 948702,
 'WindSpeed  (knots)': 8.5,
 '_id': 

 'Relative Humidity': 59.0,
 'Station': 948702,
 'WindSpeed  (knots)': 9.4,
 '_id': ObjectId('5b026118f5169e1072a55d07'),
 'fire': []}
{'Air Temperature(Celcius)': 15,
 'Date': '2017-12-02',
 'MAX': '61.7*',
 'MIN': '55.8*',
 'Max Wind Speed': 20.0,
 'Precipitation': '1.77G',
 'Relative Humidity': 56.2,
 'Station': 948702,
 'WindSpeed  (knots)': 16.9,
 '_id': ObjectId('5b026118f5169e1072a55d08'),
 'fire': []}
{'Air Temperature(Celcius)': 14,
 'Date': '2017-12-03',
 'MAX': '61.7*',
 'MIN': '55.8',
 'Max Wind Speed': 19.0,
 'Precipitation': '0.03G',
 'Relative Humidity': 48.2,
 'Station': 948702,
 'WindSpeed  (knots)': 12.5,
 '_id': ObjectId('5b026118f5169e1072a55d09'),
 'fire': []}
{'Air Temperature(Celcius)': 14,
 'Date': '2017-12-04',
 'MAX': '63.9*',
 'MIN': '51.1*',
 'Max Wind Speed': 15.0,
 'Precipitation': '0.00G',
 'Relative Humidity': 48.2,
 'Station': 948702,
 'WindSpeed  (knots)': 9.1,
 '_id': ObjectId('5b026118f5169e1072a55d0a'),
 'fire': []}
{'Air Temperature(Celcius)': 17,


In [17]:
from pprint import pprint

results = myCol2.find({})
for document in results: 
    pprint(document)

{'Confidence': 78,
 'Date': '2017-12-27',
 'Datetime': '2017-12-27T04:16:51',
 'Latitude': -37.966,
 'Longitude': 145.051,
 'Power': 26.7,
 'Surface Temperature (Celcius)': 68,
 'Surface Temperature (kelvin)': 341.8,
 '_id': ObjectId('5b026118f5169e1072a55d27')}
{'Confidence': 82,
 'Date': '2017-12-27',
 'Datetime': '2017-12-27T00:02:15',
 'Latitude': -35.541,
 'Longitude': 143.311,
 'Power': 62.0,
 'Surface Temperature (Celcius)': 63,
 'Surface Temperature (kelvin)': 336.3,
 '_id': ObjectId('5b026118f5169e1072a55d28')}
{'Confidence': 67,
 'Date': '2017-12-27',
 'Datetime': '2017-12-27T00:02:15',
 'Latitude': -35.554,
 'Longitude': 143.307,
 'Power': 23.8,
 'Surface Temperature (Celcius)': 53,
 'Surface Temperature (kelvin)': 326.8,
 '_id': ObjectId('5b026118f5169e1072a55d29')}
{'Confidence': 86,
 'Date': '2017-12-27',
 'Datetime': '2017-12-27T00:02:14',
 'Latitude': -35.543,
 'Longitude': 143.316,
 'Power': 84.2,
 'Surface Temperature (Celcius)': 67,
 'Surface Temperature (kelvin)': 3

 '_id': ObjectId('5b026118f5169e1072a55d67')}
{'Confidence': 95,
 'Date': '2017-11-30',
 'Datetime': '2017-11-30T00:20:53',
 'Latitude': -37.618,
 'Longitude': 149.281,
 'Power': 69.6,
 'Surface Temperature (Celcius)': 76,
 'Surface Temperature (kelvin)': 349.6,
 '_id': ObjectId('5b026118f5169e1072a55d68')}
{'Confidence': 81,
 'Date': '2017-11-30',
 'Datetime': '2017-11-30T00:20:53',
 'Latitude': -37.61,
 'Longitude': 149.296,
 'Power': 26.4,
 'Surface Temperature (Celcius)': 56,
 'Surface Temperature (kelvin)': 330.1,
 '_id': ObjectId('5b026118f5169e1072a55d69')}
{'Confidence': 73,
 'Date': '2017-11-30',
 'Datetime': '2017-11-30T00:20:53',
 'Latitude': -37.603,
 'Longitude': 149.324,
 'Power': 18.6,
 'Surface Temperature (Celcius)': 51,
 'Surface Temperature (kelvin)': 324.3,
 '_id': ObjectId('5b026118f5169e1072a55d6a')}
{'Confidence': 81,
 'Date': '2017-11-30',
 'Datetime': '2017-11-30T00:20:53',
 'Latitude': -37.602,
 'Longitude': 149.311,
 'Power': 26.4,
 'Surface Temperature (Celc

 'Power': 31.1,
 'Surface Temperature (Celcius)': 58,
 'Surface Temperature (kelvin)': 332.0,
 '_id': ObjectId('5b026118f5169e1072a55d9c')}
{'Confidence': 71,
 'Date': '2017-11-05',
 'Datetime': '2017-11-05T04:41:34',
 'Latitude': -36.346,
 'Longitude': 143.631,
 'Power': 14.8,
 'Surface Temperature (Celcius)': 49,
 'Surface Temperature (kelvin)': 322.4,
 '_id': ObjectId('5b026118f5169e1072a55d9d')}
{'Confidence': 90,
 'Date': '2017-11-05',
 'Datetime': '2017-11-05T04:41:19',
 'Latitude': -37.331,
 'Longitude': 143.122,
 'Power': 49.4,
 'Surface Temperature (Celcius)': 65,
 'Surface Temperature (kelvin)': 338.8,
 '_id': ObjectId('5b026118f5169e1072a55d9e')}
{'Confidence': 89,
 'Date': '2017-11-05',
 'Datetime': '2017-11-05T04:41:19',
 'Latitude': -37.329,
 'Longitude': 143.136,
 'Power': 43.8,
 'Surface Temperature (Celcius)': 62,
 'Surface Temperature (kelvin)': 335.7,
 '_id': ObjectId('5b026118f5169e1072a55d9f')}
{'Confidence': 81,
 'Date': '2017-10-28',
 'Datetime': '2017-10-28T03:5

 'Date': '2017-10-03',
 'Datetime': '2017-10-03T03:58:28',
 'Latitude': -37.236,
 'Longitude': 141.176,
 'Power': 35.1,
 'Surface Temperature (Celcius)': 37,
 'Surface Temperature (kelvin)': 310.2,
 '_id': ObjectId('5b026118f5169e1072a55dd1')}
{'Confidence': 59,
 'Date': '2017-10-03',
 'Datetime': '2017-10-03T03:58:28',
 'Latitude': -37.227,
 'Longitude': 141.151,
 'Power': 28.1,
 'Surface Temperature (Celcius)': 35,
 'Surface Temperature (kelvin)': 308.4,
 '_id': ObjectId('5b026118f5169e1072a55dd2')}
{'Confidence': 77,
 'Date': '2017-10-03',
 'Datetime': '2017-10-03T03:58:28',
 'Latitude': -37.242,
 'Longitude': 141.153,
 'Power': 56.9,
 'Surface Temperature (Celcius)': 43,
 'Surface Temperature (kelvin)': 316.9,
 '_id': ObjectId('5b026118f5169e1072a55dd3')}
{'Confidence': 76,
 'Date': '2017-10-03',
 'Datetime': '2017-10-03T03:58:28',
 'Latitude': -37.238,
 'Longitude': 141.145,
 'Power': 55.6,
 'Surface Temperature (Celcius)': 43,
 'Surface Temperature (kelvin)': 316.3,
 '_id': Objec

 'Surface Temperature (kelvin)': 321.1,
 '_id': ObjectId('5b026118f5169e1072a55e05')}
{'Confidence': 59,
 'Date': '2017-09-24',
 'Datetime': '2017-09-24T13:30:09',
 'Latitude': -37.375,
 'Longitude': 148.063,
 'Power': 23.4,
 'Surface Temperature (Celcius)': 35,
 'Surface Temperature (kelvin)': 309.1,
 '_id': ObjectId('5b026118f5169e1072a55e06')}
{'Confidence': 82,
 'Date': '2017-09-24',
 'Datetime': '2017-09-24T13:30:09',
 'Latitude': -37.336,
 'Longitude': 148.073,
 'Power': 29.2,
 'Surface Temperature (Celcius)': 38,
 'Surface Temperature (kelvin)': 311.3,
 '_id': ObjectId('5b026118f5169e1072a55e07')}
{'Confidence': 100,
 'Date': '2017-09-24',
 'Datetime': '2017-09-24T13:30:09',
 'Latitude': -37.332,
 'Longitude': 148.091,
 'Power': 51.5,
 'Surface Temperature (Celcius)': 48,
 'Surface Temperature (kelvin)': 322.0,
 '_id': ObjectId('5b026118f5169e1072a55e08')}
{'Confidence': 100,
 'Date': '2017-09-24',
 'Datetime': '2017-09-24T13:30:09',
 'Latitude': -37.363,
 'Longitude': 148.06,
 

...

{'Confidence': 76,
 'Date': '2017-04-03',
 'Datetime': '2017-04-03T03:52:10',
 'Latitude': -37.2891,
 'Longitude': 143.5697,
 'Power': 18.7,
 'Surface Temperature (Celcius)': 50,
 'Surface Temperature (kelvin)': 323.3,
 '_id': ObjectId('5b02611bf5169e1072a566a7')}
{'Confidence': 100,
 'Date': '2017-04-03',
 'Datetime': '2017-04-03T03:52:10',
 'Latitude': -37.3025,
 'Longitude': 143.5714,
 'Power': 124.9,
 'Surface Temperature (Celcius)': 98,
 'Surface Temperature (kelvin)': 372.0,
 '_id': ObjectId('5b02611bf5169e1072a566a8')}
{'Confidence': 100,
 'Date': '2017-04-03',
 'Datetime': '2017-04-03T03:52:10',
 'Latitude': -37.383,
 'Longitude': 145.9089,
 'Power': 104.5,
 'Surface Temperature (Celcius)': 89,
 'Surface Temperature (kelvin)': 362.4,
 '_id': ObjectId('5b02611bf5169e1072a566a9')}
{'Confidence': 85,
 'Date': '2017-04-03',
 'Datetime': '2017-04-03T03:52:10',
 'Latitude': -37.7216,
 'Longitude': 143.4272,
 'Power': 33.0,
 'Surface Temperature (Celcius)': 59,
 'Surface Temperature (

 'Power': 21.6,
 'Surface Temperature (Celcius)': 46,
 'Surface Temperature (kelvin)': 319.2,
 '_id': ObjectId('5b02611bf5169e1072a566db')}
{'Confidence': 77,
 'Date': '2017-04-01',
 'Datetime': '2017-04-01T04:02:50',
 'Latitude': -36.1256,
 'Longitude': 145.2444,
 'Power': 24.0,
 'Surface Temperature (Celcius)': 53,
 'Surface Temperature (kelvin)': 326.4,
 '_id': ObjectId('5b02611bf5169e1072a566dc')}
{'Confidence': 58,
 'Date': '2017-04-01',
 'Datetime': '2017-04-01T04:02:40',
 'Latitude': -36.2044,
 'Longitude': 145.7706,
 'Power': 19.1,
 'Surface Temperature (Celcius)': 51,
 'Surface Temperature (kelvin)': 324.7,
 '_id': ObjectId('5b02611bf5169e1072a566dd')}
{'Confidence': 57,
 'Date': '2017-04-01',
 'Datetime': '2017-04-01T04:02:40',
 'Latitude': -36.5245,
 'Longitude': 143.1556,
 'Power': 12.3,
 'Surface Temperature (Celcius)': 43,
 'Surface Temperature (kelvin)': 316.5,
 '_id': ObjectId('5b02611bf5169e1072a566de')}
{'Confidence': 50,
 'Date': '2017-04-01',
 'Datetime': '2017-04-0

 'Date': '2017-03-28',
 'Datetime': '2017-03-28T04:27:20',
 'Latitude': -37.9526,
 'Longitude': 143.597,
 'Power': 158.5,
 'Surface Temperature (Celcius)': 107,
 'Surface Temperature (kelvin)': 380.9,
 '_id': ObjectId('5b02611bf5169e1072a56710')}
{'Confidence': 77,
 'Date': '2017-03-28',
 'Datetime': '2017-03-28T04:27:20',
 'Latitude': -36.4811,
 'Longitude': 142.2606,
 'Power': 15.3,
 'Surface Temperature (Celcius)': 50,
 'Surface Temperature (kelvin)': 324.1,
 '_id': ObjectId('5b02611bf5169e1072a56711')}
{'Confidence': 76,
 'Date': '2017-03-28',
 'Datetime': '2017-03-28T04:27:20',
 'Latitude': -36.4483,
 'Longitude': 142.2303,
 'Power': 14.5,
 'Surface Temperature (Celcius)': 49,
 'Surface Temperature (kelvin)': 322.9,
 '_id': ObjectId('5b02611bf5169e1072a56712')}
{'Confidence': 100,
 'Date': '2017-03-28',
 'Datetime': '2017-03-28T04:27:10',
 'Latitude': -37.6269,
 'Longitude': 143.4348,
 'Power': 160.7,
 'Surface Temperature (Celcius)': 108,
 'Surface Temperature (kelvin)': 382.0,
 

 'Surface Temperature (kelvin)': 332.8,
 '_id': ObjectId('5b02611bf5169e1072a56744')}
{'Confidence': 100,
 'Date': '2017-03-25',
 'Datetime': '2017-03-25T03:57:10',
 'Latitude': -37.8122,
 'Longitude': 146.0807,
 'Power': 180.6,
 'Surface Temperature (Celcius)': 111,
 'Surface Temperature (kelvin)': 384.5,
 '_id': ObjectId('5b02611bf5169e1072a56745')}
{'Confidence': 95,
 'Date': '2017-03-25',
 'Datetime': '2017-03-25T03:57:10',
 'Latitude': -37.8774,
 'Longitude': 145.8213,
 'Power': 73.6,
 'Surface Temperature (Celcius)': 77,
 'Surface Temperature (kelvin)': 350.7,
 '_id': ObjectId('5b02611bf5169e1072a56746')}
{'Confidence': 75,
 'Date': '2017-03-25',
 'Datetime': '2017-03-25T03:56:50',
 'Latitude': -37.5742,
 'Longitude': 144.7536,
 'Power': 16.2,
 'Surface Temperature (Celcius)': 49,
 'Surface Temperature (kelvin)': 323.0,
 '_id': ObjectId('5b02611bf5169e1072a56747')}
{'Confidence': 100,
 'Date': '2017-03-25',
 'Datetime': '2017-03-25T03:56:40',
 'Latitude': -37.8881,
 'Longitude': 

{'Confidence': 95,
 'Date': '2017-03-14',
 'Datetime': '2017-03-14T04:16:30',
 'Latitude': -36.9959,
 'Longitude': 148.2118,
 'Power': 65.9,
 'Surface Temperature (Celcius)': 75,
 'Surface Temperature (kelvin)': 349.1,
 '_id': ObjectId('5b02611bf5169e1072a56776')}
{'Confidence': 89,
 'Date': '2017-03-14',
 'Datetime': '2017-03-14T04:16:20',
 'Latitude': -34.3654,
 'Longitude': 141.543,
 'Power': 25.7,
 'Surface Temperature (Celcius)': 65,
 'Surface Temperature (kelvin)': 338.5,
 '_id': ObjectId('5b02611bf5169e1072a56777')}
{'Confidence': 73,
 'Date': '2017-03-14',
 'Datetime': '2017-03-14T04:14:40',
 'Latitude': -37.0228,
 'Longitude': 148.1996,
 'Power': 24.0,
 'Surface Temperature (Celcius)': 52,
 'Surface Temperature (kelvin)': 326.1,
 '_id': ObjectId('5b02611bf5169e1072a56778')}
{'Confidence': 81,
 'Date': '2017-03-14',
 'Datetime': '2017-03-14T04:14:40',
 'Latitude': -34.3539,
 'Longitude': 141.5629,
 'Power': 10.3,
 'Surface Temperature (Celcius)': 55,
 'Surface Temperature (kelv

In [18]:
#B4
#Solution for A2:
results = myCol1.find({"Date":"2017-12-15"},{"fire":0})
for document in results:  
    pprint(document)

{'Air Temperature(Celcius)': 18,
 'Date': '2017-12-15',
 'MAX': '74.5*',
 'MIN': '53.1',
 'Max Wind Speed': 14.0,
 'Precipitation': '0.00I',
 'Relative Humidity': 52.0,
 'Station': 948702,
 'WindSpeed  (knots)': 7.1,
 '_id': ObjectId('5b026118f5169e1072a55d15')}


In [19]:
#A3
results = myCol2.find({"Surface Temperature (Celcius)":{'$gte':65,'$lte':100}}, 
                      {"_id":0,"Latitude":1,"Longitude":1,"Confidence":1})
for document in results:  
    pprint(document)

{'Confidence': 78, 'Latitude': -37.966, 'Longitude': 145.051}
{'Confidence': 86, 'Latitude': -35.543, 'Longitude': 143.316}
{'Confidence': 93, 'Latitude': -37.875, 'Longitude': 142.51}
{'Confidence': 95, 'Latitude': -37.613, 'Longitude': 149.305}
{'Confidence': 90, 'Latitude': -37.624, 'Longitude': 149.314}
{'Confidence': 93, 'Latitude': -38.057, 'Longitude': 144.211}
{'Confidence': 92, 'Latitude': -37.95, 'Longitude': 142.366}
{'Confidence': 100, 'Latitude': -36.282, 'Longitude': 146.157}
{'Confidence': 100, 'Latitude': -37.642, 'Longitude': 149.263}
{'Confidence': 100, 'Latitude': -37.634, 'Longitude': 149.237}
{'Confidence': 98, 'Latitude': -37.605, 'Longitude': 149.302}
{'Confidence': 99, 'Latitude': -37.6, 'Longitude': 149.325}
{'Confidence': 95, 'Latitude': -37.618, 'Longitude': 149.281}
{'Confidence': 100, 'Latitude': -37.606, 'Longitude': 149.312}
{'Confidence': 97, 'Latitude': -37.61, 'Longitude': 149.307}
{'Confidence': 99, 'Latitude': -37.609, 'Longitude': 149.32}
{'Confiden

In [20]:
#A4
results=myCol1.aggregate([{'$match':{"Date":{"$in":["2017-12-16","2017-12-15"]}}},
                          { '$lookup': { 'from':"Fire", 'localField':"Date", 'foreignField':"Date", 'as':"match" } },
                          { '$project' : {"_id":0,"match.Surface Temperature (Celcius)":1,
                                          "Air Temperature(Celcius)":1,
                                          "Relative Humidity":1,
                                          "Max Wind Speed":1 } }])
for document in results:  
    pprint(document)

{'Air Temperature(Celcius)': 18,
 'Max Wind Speed': 14.0,
 'Relative Humidity': 52.0,
 'match': [{'Surface Temperature (Celcius)': 42},
           {'Surface Temperature (Celcius)': 36},
           {'Surface Temperature (Celcius)': 38},
           {'Surface Temperature (Celcius)': 40}]}
{'Air Temperature(Celcius)': 18,
 'Max Wind Speed': 13.0,
 'Relative Humidity': 53.7,
 'match': [{'Surface Temperature (Celcius)': 43},
           {'Surface Temperature (Celcius)': 33},
           {'Surface Temperature (Celcius)': 54},
           {'Surface Temperature (Celcius)': 73},
           {'Surface Temperature (Celcius)': 55},
           {'Surface Temperature (Celcius)': 75},
           {'Surface Temperature (Celcius)': 55},
           {'Surface Temperature (Celcius)': 66},
           {'Surface Temperature (Celcius)': 56},
           {'Surface Temperature (Celcius)': 60},
           {'Surface Temperature (Celcius)': 73},
           {'Surface Temperature (Celcius)': 48},
           {'Surface Temper

In [21]:
#A5
results=myCol2.aggregate([{'$match':{"Confidence":{'$gte':80,'$lte':100}}},
                          {'$lookup': { 'from':"Climate", 'localField':"Date", 'foreignField':"Date", 'as':"match" } },
                          {'$project': {"_id":0, "Datetime":1, 
                                        "match.Air Temperature(Celcius)":1, 
                                        "Surface Temperature (Celcius)":1, 
                                        "Confidence":1 } }])
for document in results:  
    pprint(document)

{'Confidence': 82,
 'Datetime': '2017-12-27T00:02:15',
 'Surface Temperature (Celcius)': 63,
 'match': [{'Air Temperature(Celcius)': 28}]}
{'Confidence': 86,
 'Datetime': '2017-12-27T00:02:14',
 'Surface Temperature (Celcius)': 67,
 'match': [{'Air Temperature(Celcius)': 28}]}
{'Confidence': 80,
 'Datetime': '2017-12-25T04:29:08',
 'Surface Temperature (Celcius)': 54,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 94,
 'Datetime': '2017-12-16T15:38:39',
 'Surface Temperature (Celcius)': 43,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 93,
 'Datetime': '2017-12-16T04:35:13',
 'Surface Temperature (Celcius)': 73,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 84,
 'Datetime': '2017-12-16T04:34:58',
 'Surface Temperature (Celcius)': 55,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 95,
 'Datetime': '2017-12-16T04:34:58',
 'Surface Temperature (Celcius)': 75,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 90,
 'Dateti

{'Confidence': 100,
 'Datetime': '2017-09-24T15:07:47',
 'Surface Temperature (Celcius)': 65,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 90,
 'Datetime': '2017-09-24T15:07:47',
 'Surface Temperature (Celcius)': 41,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 99,
 'Datetime': '2017-09-24T15:07:47',
 'Surface Temperature (Celcius)': 61,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 94,
 'Datetime': '2017-09-24T15:07:45',
 'Surface Temperature (Celcius)': 43,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 100,
 'Datetime': '2017-09-24T15:07:45',
 'Surface Temperature (Celcius)': 61,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 100,
 'Datetime': '2017-09-24T13:30:10',
 'Surface Temperature (Celcius)': 47,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 82,
 'Datetime': '2017-09-24T13:30:09',
 'Surface Temperature (Celcius)': 38,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 100,
 'Da

 'match': [{'Air Temperature(Celcius)': 10}]}
{'Confidence': 100,
 'Datetime': '2017-05-13T04:45:40',
 'Surface Temperature (Celcius)': 102,
 'match': [{'Air Temperature(Celcius)': 9}]}
{'Confidence': 95,
 'Datetime': '2017-05-13T04:43:30',
 'Surface Temperature (Celcius)': 77,
 'match': [{'Air Temperature(Celcius)': 9}]}
{'Confidence': 100,
 'Datetime': '2017-05-13T04:41:50',
 'Surface Temperature (Celcius)': 98,
 'match': [{'Air Temperature(Celcius)': 9}]}
{'Confidence': 100,
 'Datetime': '2017-05-13T04:40:20',
 'Surface Temperature (Celcius)': 120,
 'match': [{'Air Temperature(Celcius)': 9}]}
{'Confidence': 100,
 'Datetime': '2017-05-13T04:40:10',
 'Surface Temperature (Celcius)': 90,
 'match': [{'Air Temperature(Celcius)': 9}]}
{'Confidence': 81,
 'Datetime': '2017-05-13T04:39:50',
 'Surface Temperature (Celcius)': 55,
 'match': [{'Air Temperature(Celcius)': 9}]}
{'Confidence': 83,
 'Datetime': '2017-05-13T04:39:30',
 'Surface Temperature (Celcius)': 63,
 'match': [{'Air Temperatur

 'match': [{'Air Temperature(Celcius)': 12}]}
{'Confidence': 87,
 'Datetime': '2017-05-08T04:24:00',
 'Surface Temperature (Celcius)': 62,
 'match': [{'Air Temperature(Celcius)': 12}]}
{'Confidence': 80,
 'Datetime': '2017-05-08T04:20:40',
 'Surface Temperature (Celcius)': 54,
 'match': [{'Air Temperature(Celcius)': 12}]}
{'Confidence': 83,
 'Datetime': '2017-05-08T04:20:20',
 'Surface Temperature (Celcius)': 56,
 'match': [{'Air Temperature(Celcius)': 12}]}
{'Confidence': 86,
 'Datetime': '2017-05-08T04:20:10',
 'Surface Temperature (Celcius)': 60,
 'match': [{'Air Temperature(Celcius)': 12}]}
{'Confidence': 91,
 'Datetime': '2017-05-08T04:20:10',
 'Surface Temperature (Celcius)': 68,
 'match': [{'Air Temperature(Celcius)': 12}]}
{'Confidence': 100,
 'Datetime': '2017-05-08T04:20:10',
 'Surface Temperature (Celcius)': 101,
 'match': [{'Air Temperature(Celcius)': 12}]}
{'Confidence': 100,
 'Datetime': '2017-05-08T04:20:10',
 'Surface Temperature (Celcius)': 115,
 'match': [{'Air Temper

 'Surface Temperature (Celcius)': 43,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 100,
 'Datetime': '2017-04-23T12:50:40',
 'Surface Temperature (Celcius)': 55,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 88,
 'Datetime': '2017-04-23T05:03:40',
 'Surface Temperature (Celcius)': 64,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 93,
 'Datetime': '2017-04-23T05:03:10',
 'Surface Temperature (Celcius)': 72,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 99,
 'Datetime': '2017-04-23T05:02:50',
 'Surface Temperature (Celcius)': 86,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 100,
 'Datetime': '2017-04-23T05:02:50',
 'Surface Temperature (Celcius)': 101,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 81,
 'Datetime': '2017-04-23T05:02:50',
 'Surface Temperature (Celcius)': 54,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 87,
 'Datetime': '2017-04-22T04:20:20',
 'Surface Temperature (C

...

{'Confidence': 100,
 'Datetime': '2017-04-13T04:33:50',
 'Surface Temperature (Celcius)': 88,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 81,
 'Datetime': '2017-04-13T04:33:40',
 'Surface Temperature (Celcius)': 54,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 84,
 'Datetime': '2017-04-13T04:33:40',
 'Surface Temperature (Celcius)': 58,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 91,
 'Datetime': '2017-04-13T04:33:30',
 'Surface Temperature (Celcius)': 69,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 99,
 'Datetime': '2017-04-13T04:33:30',
 'Surface Temperature (Celcius)': 85,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 90,
 'Datetime': '2017-04-13T04:33:30',
 'Surface Temperature (Celcius)': 66,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 100,
 'Datetime': '2017-04-13T04:33:20',
 'Surface Temperature (Celcius)': 96,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 89,
 'Date

 'Datetime': '2017-04-13T04:26:50',
 'Surface Temperature (Celcius)': 54,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 84,
 'Datetime': '2017-04-13T04:26:50',
 'Surface Temperature (Celcius)': 58,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 85,
 'Datetime': '2017-04-13T04:26:50',
 'Surface Temperature (Celcius)': 59,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 100,
 'Datetime': '2017-04-13T04:26:40',
 'Surface Temperature (Celcius)': 104,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 90,
 'Datetime': '2017-04-13T04:26:40',
 'Surface Temperature (Celcius)': 66,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 80,
 'Datetime': '2017-04-13T04:26:40',
 'Surface Temperature (Celcius)': 53,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 97,
 'Datetime': '2017-04-13T04:26:40',
 'Surface Temperature (Celcius)': 80,
 'match': [{'Air Temperature(Celcius)': 16}]}
{'Confidence': 100,
 'Datetime': '2017-04-13

 'Surface Temperature (Celcius)': 98,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 95,
 'Datetime': '2017-04-12T03:54:10',
 'Surface Temperature (Celcius)': 77,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 87,
 'Datetime': '2017-04-12T03:50:00',
 'Surface Temperature (Celcius)': 63,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 95,
 'Datetime': '2017-04-12T03:50:00',
 'Surface Temperature (Celcius)': 75,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 86,
 'Datetime': '2017-04-12T03:50:00',
 'Surface Temperature (Celcius)': 61,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 92,
 'Datetime': '2017-04-12T03:47:50',
 'Surface Temperature (Celcius)': 70,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 84,
 'Datetime': '2017-04-12T03:47:50',
 'Surface Temperature (Celcius)': 58,
 'match': [{'Air Temperature(Celcius)': 14}]}
{'Confidence': 84,
 'Datetime': '2017-04-12T03:47:30',
 'Surface Temperature (Celc

 'Surface Temperature (Celcius)': 55,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 98,
 'Datetime': '2017-04-05T13:03:00',
 'Surface Temperature (Celcius)': 45,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 100,
 'Datetime': '2017-04-05T13:03:00',
 'Surface Temperature (Celcius)': 55,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 81,
 'Datetime': '2017-04-05T13:03:00',
 'Surface Temperature (Celcius)': 39,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 88,
 'Datetime': '2017-04-05T13:02:40',
 'Surface Temperature (Celcius)': 42,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 80,
 'Datetime': '2017-04-05T13:02:40',
 'Surface Temperature (Celcius)': 39,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 87,
 'Datetime': '2017-04-05T05:16:50',
 'Surface Temperature (Celcius)': 88,
 'match': [{'Air Temperature(Celcius)': 17}]}
{'Confidence': 93,
 'Datetime': '2017-04-05T05:15:30',
 'Surface Temperature (Cel

 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 86,
 'Datetime': '2017-03-28T04:33:40',
 'Surface Temperature (Celcius)': 60,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 92,
 'Datetime': '2017-03-28T04:33:30',
 'Surface Temperature (Celcius)': 71,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 95,
 'Datetime': '2017-03-28T04:33:30',
 'Surface Temperature (Celcius)': 76,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 93,
 'Datetime': '2017-03-28T04:32:20',
 'Surface Temperature (Celcius)': 73,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 83,
 'Datetime': '2017-03-28T04:30:50',
 'Surface Temperature (Celcius)': 56,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 80,
 'Datetime': '2017-03-28T04:30:20',
 'Surface Temperature (Celcius)': 54,
 'match': [{'Air Temperature(Celcius)': 18}]}
{'Confidence': 94,
 'Datetime': '2017-03-28T04:30:10',
 'Surface Temperature (Celcius)': 74,
 'match': [{'Air Temperatur

In [22]:
#A6
results=myCol2.find().sort([("Surface Temperature (Celcius)",-1)]).limit(10)
for document in results:  
    pprint(document)

{'Confidence': 100,
 'Date': '2017-04-18',
 'Datetime': '2017-04-18T04:52:00',
 'Latitude': -38.1665,
 'Longitude': 143.062,
 'Power': 239.8,
 'Surface Temperature (Celcius)': 124,
 'Surface Temperature (kelvin)': 397.5,
 '_id': ObjectId('5b026119f5169e1072a561ca')}
{'Confidence': 100,
 'Date': '2017-04-04',
 'Datetime': '2017-04-04T04:32:50',
 'Latitude': -36.343,
 'Longitude': 142.1986,
 'Power': 233.4,
 'Surface Temperature (Celcius)': 123,
 'Surface Temperature (kelvin)': 396.3,
 '_id': ObjectId('5b02611bf5169e1072a56674')}
{'Confidence': 100,
 'Date': '2017-05-01',
 'Datetime': '2017-05-01T04:14:20',
 'Latitude': -36.9318,
 'Longitude': 143.0907,
 'Power': 236.0,
 'Surface Temperature (Celcius)': 122,
 'Surface Temperature (kelvin)': 396.0,
 '_id': ObjectId('5b026119f5169e1072a5613c')}
{'Confidence': 100,
 'Date': '2017-03-18',
 'Datetime': '2017-03-18T03:50:50',
 'Latitude': -37.017,
 'Longitude': 148.1297,
 'Power': 224.3,
 'Surface Temperature (Celcius)': 121,
 'Surface Tempera

In [23]:
#A7
results=myCol2.aggregate([{'$group':{'_id':"$Date", 'count':{'$sum':1}}}])
for document in results:  
    pprint(document)

{'_id': '2017-03-07', 'count': 1}
{'_id': '2017-03-09', 'count': 3}
{'_id': '2017-03-10', 'count': 8}
{'_id': '2017-03-12', 'count': 5}
{'_id': '2017-03-13', 'count': 2}
{'_id': '2017-03-18', 'count': 3}
{'_id': '2017-03-25', 'count': 13}
{'_id': '2017-03-26', 'count': 17}
{'_id': '2017-03-29', 'count': 1}
{'_id': '2017-04-01', 'count': 7}
{'_id': '2017-04-02', 'count': 5}
{'_id': '2017-04-04', 'count': 89}
{'_id': '2017-04-11', 'count': 24}
{'_id': '2017-04-12', 'count': 69}
{'_id': '2017-04-13', 'count': 357}
{'_id': '2017-04-15', 'count': 69}
{'_id': '2017-04-03', 'count': 72}
{'_id': '2017-04-16', 'count': 18}
{'_id': '2017-03-08', 'count': 2}
{'_id': '2017-04-18', 'count': 325}
{'_id': '2017-04-19', 'count': 50}
{'_id': '2017-04-17', 'count': 38}
{'_id': '2017-04-20', 'count': 31}
{'_id': '2017-04-22', 'count': 2}
{'_id': '2017-04-23', 'count': 19}
{'_id': '2017-04-24', 'count': 8}
{'_id': '2017-04-26', 'count': 1}
{'_id': '2017-04-29', 'count': 3}
{'_id': '2017-05-01', 'count': 2

In [24]:
#A8
results=myCol2.aggregate([{'$group':{'_id':"$Date",'avg':{'$avg':"$Surface Temperature (Celcius)"}}}])
for document in results:  
    pprint(document)

{'_id': '2017-03-07', 'avg': 64.0}
{'_id': '2017-03-09', 'avg': 46.666666666666664}
{'_id': '2017-03-10', 'avg': 69.375}
{'_id': '2017-03-12', 'avg': 88.2}
{'_id': '2017-03-13', 'avg': 38.5}
{'_id': '2017-03-18', 'avg': 79.33333333333333}
{'_id': '2017-03-25', 'avg': 66.0}
{'_id': '2017-03-26', 'avg': 56.88235294117647}
{'_id': '2017-03-29', 'avg': 51.0}
{'_id': '2017-04-01', 'avg': 46.714285714285715}
{'_id': '2017-04-02', 'avg': 45.2}
{'_id': '2017-04-04', 'avg': 62.57303370786517}
{'_id': '2017-04-11', 'avg': 46.291666666666664}
{'_id': '2017-04-12', 'avg': 52.69565217391305}
{'_id': '2017-04-13', 'avg': 58.57983193277311}
{'_id': '2017-04-15', 'avg': 59.57971014492754}
{'_id': '2017-04-03', 'avg': 58.44444444444444}
{'_id': '2017-04-16', 'avg': 48.72222222222222}
{'_id': '2017-03-08', 'avg': 51.5}
{'_id': '2017-04-18', 'avg': 53.36615384615384}
{'_id': '2017-04-19', 'avg': 54.16}
{'_id': '2017-04-17', 'avg': 50.921052631578945}
{'_id': '2017-04-20', 'avg': 56.58064516129032}
{'_id'

In [25]:
#paralel for A2-Find climate data on 15th December 2017

def s_hash(r,n):
    result = r%n
    return result

In [26]:
import time

def h_partition(myCol,n):
    result = []
    for i in range(n):
        result.append([])   
    data=myCol.find({},{"fire":0})   
    for x in data:
        newM = time.strptime(x['Date'], '%Y-%m-%d')
        mon = newM.tm_mon
        h = s_hash(mon,n)
        result[h].append(x)
    return result

In [27]:
from datetime import datetime 

def linear_search(data,key):
    matched_record = None
    for x in data:
        if datetime.strptime(x['Date'],'%Y-%m-%d') == datetime.strptime(key, '%Y-%m-%d'):
            matched_record = x
            break
    return matched_record

In [28]:
from multiprocessing import Pool

def paralell_search_11 (data, key, n_processor):
    results = []
    pool = Pool(processes = n_processor)
    DD = h_partition(data, n_processor)
    key_mon = (time.strptime(key, '%Y-%m-%d').tm_mon)
    key_hash = s_hash(key_mon, n_processor)
    
    d = DD[key_hash]
    results = pool.apply(linear_search, [d, key])
    return results

In [29]:
data=myCol1
key='2017-12-15'
n_processor=3
paralell_search_11 (data, key, n_processor)

{'Air Temperature(Celcius)': 18,
 'Date': '2017-12-15',
 'MAX': '74.5*',
 'MIN': '53.1',
 'Max Wind Speed': 14.0,
 'Precipitation': '0.00I',
 'Relative Humidity': 52.0,
 'Station': 948702,
 'WindSpeed  (knots)': 7.1,
 '_id': ObjectId('5b026118f5169e1072a55d15')}

In [30]:
db.Climate.drop()

In [31]:
db.Fire.drop()

In [32]:
client.drop_database('TaskB_db')

In [41]:
#Testing taskC
db = client.TaskC_db

In [42]:
myCol1 = db.ClimateData
myCol2 = db.FireData

In [43]:
results=myCol2.aggregate([{'$match':{"Confidence":{'$gte':80,'$lte':100}}},
                          {'$lookup': { 'from':"ClimateData", 'localField':"Date", 'foreignField':"Date", 'as':"match" } },
                          {'$project': {"_id":0, "Datetime":1, 
                                        "match.Air Temperature(Celcius)":1, 
                                        "Surface Temperature (Celcius)":1, 
                                        "Confidence":1 } }])
for document in results:  
    pprint(document)

{'Confidence': 82.0,
 'Datetime': '2018-05-21 16:09:14.687604',
 'Surface Temperature (Celcius)': 63.0,
 'match': [{'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 15.0},
           {'Air Temperature(Celcius)': 16.0},
           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 26.0},
           {'Air Temperature(Celcius)': 32.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 22.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 16.0},
           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 16.0},
           {'Air Temperature(Celcius)': 19.0},
   

           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 23.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 22.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 23.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 25.0},
           {'Air Temperature(Celcius)': 28.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 24.0},
           {'

           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 23.0},
           {'Air Temperature(Celcius)': 23.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 17.0}]}
{'Confidence': 100.0,
 'Datetime': '2018-05-21 16:09:14.694435',
 'Surface Temperature (Celcius)': 54.0,
 'match': [{'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 15.0},
           {'Air Temperature(Celcius)': 16.0},
           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 26.0},
           {'Air Temperature(Celcius)': 32.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 22.0},
 

           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 22.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 16.0},
           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 16.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 16.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 23.0},
           {'Air Temperature(Celcius)': 25.0},
           {'Air Temperature(Celcius)': 16.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 22.0},
           {'

           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 23.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 25.0},
           {'Air Temperature(Celcius)': 28.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 24.0},
           {'Air Temperature(Celcius)': 23.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 23.0},
           {'Air Temperature(Celcius)': 23.0},
           {'Air Temperature(Celcius)': 17.0},
           {'

...

           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 28.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 25.0}]}
{'Confidence': 100.0,
 'Datetime': '2018-05-21 16:09:18.090007',
 'Surface Temperature (Celcius)': 98.0,
 'match': []}
{'Confidence': 83.0,
 'Datetime': '2018-05-21 16:09:17.858471',
 'Surface Temperature (Celcius)': 56.0,
 'match': [{'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 14.0},
           {'Air Temperature(Celcius)': 9.0},
           {'Air Temperature(Celcius)': 12.0},
           {'Air Temperature(Celcius)': 11.0},
           {'Air Temperature(Celcius)': 13.0},
           {'Air Temperat

           {'Air Temperature(Celcius)': 12.0},
           {'Air Temperature(Celcius)': 22.0},
           {'Air Temperature(Celcius)': 11.0},
           {'Air Temperature(Celcius)': 15.0},
           {'Air Temperature(Celcius)': 13.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 19.0},
           {'Air Temperature(Celcius)': 11.0},
           {'Air Temperature(Celcius)': 12.0},
           {'Air Temperature(Celcius)': 13.0},
           {'Air Temperature(Celcius)': 11.0},
           {'Air Temperature(Celcius)': 13.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 12.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 12.0},
           {'Air Temperature(Celcius)': 11.0},
           {'Air Temperature(Celcius)': 13.0},
           {'Air Temperature(Celcius)': 11.0},
           {'Air Temperature(Celcius)': 15.0},
           {'Air Temperature(Celcius)': 13.0},
           {'

           {'Air Temperature(Celcius)': 28.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 18.0},
           {'Air Temperature(Celcius)': 21.0},
           {'Air Temperature(Celcius)': 25.0}]}
{'Confidence': 82.0,
 'Datetime': '2018-05-21 16:09:18.092710',
 'Surface Temperature (Celcius)': 55.0,
 'match': []}
{'Confidence': 84.0,
 'Datetime': '2018-05-21 16:09:17.861160',
 'Surface Temperature (Celcius)': 80.0,
 'match': [{'Air Temperature(Celcius)': 20.0},
           {'Air Temperature(Celcius)': 17.0},
           {'Air Temperature(Celcius)': 14.0},
           {'Air Temperature(Celcius)': 9.0},
           {'Air Temperature(Celcius)': 12.0},
           {'Air Temperature(Celcius)': 11.0},
           {'Air Temperature(Celcius)': 13.0},
           {'Air Temperature(Celcius)': 15.0},
           {'Air Temperature(Celcius)': 14.0},
           {'Air Temperature(Celcius)': 13.0},
           {'Air Temperatu

{'Confidence': 100.0,
 'Datetime': '2018-05-21 16:09:18.506856',
 'Surface Temperature (Celcius)': 49.0,
 'match': []}
{'Confidence': 86.0,
 'Datetime': '2018-05-21 16:09:18.307723',
 'Surface Temperature (Celcius)': 41.0,
 'match': []}
{'Confidence': 100.0,
 'Datetime': '2018-05-21 16:09:18.507291',
 'Surface Temperature (Celcius)': 55.0,
 'match': []}
{'Confidence': 98.0,
 'Datetime': '2018-05-21 16:09:18.507537',
 'Surface Temperature (Celcius)': 45.0,
 'match': []}
{'Confidence': 86.0,
 'Datetime': '2018-05-21 16:09:18.308063',
 'Surface Temperature (Celcius)': 41.0,
 'match': []}
{'Confidence': 85.0,
 'Datetime': '2018-05-21 16:09:18.713851',
 'Surface Temperature (Celcius)': 59.0,
 'match': []}
{'Confidence': 100.0,
 'Datetime': '2018-05-21 16:09:18.507628',
 'Surface Temperature (Celcius)': 55.0,
 'match': []}
{'Confidence': 97.0,
 'Datetime': '2018-05-21 16:09:18.308214',
 'Surface Temperature (Celcius)': 45.0,
 'match': []}
{'Confidence': 81.0,
 'Datetime': '2018-05-21 16:09:1

{'Confidence': 86.0,
 'Datetime': '2018-05-21 16:09:18.318418',
 'Surface Temperature (Celcius)': 68.0,
 'match': []}
{'Confidence': 89.0,
 'Datetime': '2018-05-21 16:09:18.517420',
 'Surface Temperature (Celcius)': 65.0,
 'match': []}
{'Confidence': 85.0,
 'Datetime': '2018-05-21 16:09:18.318754',
 'Surface Temperature (Celcius)': 59.0,
 'match': []}
{'Confidence': 90.0,
 'Datetime': '2018-05-21 16:09:18.318967',
 'Surface Temperature (Celcius)': 67.0,
 'match': []}
{'Confidence': 86.0,
 'Datetime': '2018-05-21 16:09:18.725241',
 'Surface Temperature (Celcius)': 61.0,
 'match': []}
{'Confidence': 96.0,
 'Datetime': '2018-05-21 16:09:18.517876',
 'Surface Temperature (Celcius)': 78.0,
 'match': []}
{'Confidence': 90.0,
 'Datetime': '2018-05-21 16:09:18.319238',
 'Surface Temperature (Celcius)': 66.0,
 'match': []}
{'Confidence': 85.0,
 'Datetime': '2018-05-21 16:09:18.517951',
 'Surface Temperature (Celcius)': 66.0,
 'match': []}
{'Confidence': 84.0,
 'Datetime': '2018-05-21 16:09:18.5